In [1]:
!pip install newspaper3k

  Using cached newspaper3k-0.2.8-py3-none-any.whl (211 kB)
  Using cached feedparser-6.0.2-py3-none-any.whl (80 kB)
  Using cached jieba3k-0.35.1.zip (7.4 MB)
  Using cached cssselect-1.1.0-py2.py3-none-any.whl (16 kB)
  Using cached tinysegmenter-0.3.tar.gz (16 kB)
  Using cached tldextract-3.1.0-py2.py3-none-any.whl (87 kB)
  Using cached feedfinder2-0.0.4.tar.gz (3.3 kB)
  Using cached sgmllib3k-1.0.0.tar.gz (5.8 kB)
  Using cached requests_file-1.5.1-py2.py3-none-any.whl (3.7 kB)
  Created wheel for jieba3k: filename=jieba3k-0.35.1-py3-none-any.whl size=7398411 sha256=068d6749892c5d264d9672861528d06f124bad64a4d84bcd46d7db01bae512c8
  Stored in directory: c:\users\dell\appdata\local\pip\cache\wheels\1f\7e\0c\54f3b0f5164278677899f2db08f2b07943ce2d024a3c862afb
  Created wheel for tinysegmenter: filename=tinysegmenter-0.3-py3-none-any.whl size=13543 sha256=2821d3a7bc22d98d60c2bb77a2d5f5277b1fe500226c0b55597a658061910cf9
  Stored in directory: c:\users\dell\appdata\local\pip\cache\wheel

In [2]:
!curl https://raw.githubusercontent.com/codelucas/newspaper/master/download_corpora.py | python

Finished.


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100   657  100   657    0     0   1368      0 --:--:-- --:--:-- --:--:--  1368
[nltk_data] Downloading package brown to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package maxent_treebank_pos_tagger to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package maxent_treebank_pos_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package movie_reviews to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package movie_reviews is already up-to-date!
[n

In [1]:
from newspaper import Article
import pandas as pd
from bs4 import BeautifulSoup
import urllib.request

In [2]:
def crawl_by_url(url, title):
    article = Article(url, language='vi')
    article.download()
    article.parse()
    contents = str(article.text).replace("\n","")
    article.nlp()
    # replace
    char_to_replace = {':': '',
                       '/': '',
                       '\\': '',
                      '*': '',
                      '?': '',
                      '"': '',
                      '<': '',
                      '>': '',
                      '|': ''}
    for key, value in char_to_replace.items():
        # Replace key character with value character in string
        title = title.replace(key, value)

    # write txt
    # https://vnexpress.net
    if(url.find('https://vnexpress.net/') != -1):
        output = "data/text/vnexpress/" + title  + ".txt"
        f = open(output, "w+", encoding='utf-8')
        f.write(str(url)+"\n")
        f.write(title+"\n")
        f.write(contents)
        f.close()
    elif(url.find('https://thanhnien.vn/') != -1):
        output = "data/text/thanhnien/" + title  + ".txt"
        f = open(output, "w+", encoding='utf-8')
        f.write(str(url)+"\n")
        f.write(title+"\n")
        f.write(contents)
    elif(url.find('https://vietnamnet.vn/') != -1):
        output = "data/text/vietnamnet/" + title  + ".txt"
        f = open(output, "w+", encoding='utf-8')
        f.write(str(url)+"\n")
        f.write(title+"\n")
        f.write(contents)

In [3]:
# VNEXPRESS
def get_links_in_page_vnexpress(url):
    page = urllib.request.urlopen(url)
    soup = BeautifulSoup(page, 'html.parser')
    # <section>
    sections = soup.find_all('section', attrs={'class':'section section_container mt15'})
    # <h3>
    h3_all = []
    for section in sections:
        h3_all.extend(section.find_all('h3', attrs={'class':'title-news'}))
    # <a>
    a_all = []
    results = [[]]
    for h3 in h3_all:
        a_all.extend(h3.find_all('a', attrs={'class':''}))
    for a in a_all:
        title = a.get('title')
        link = a.get('href')
        print('Title: {} - Link: {}'.format(title, link))
        results.append([title,link])
    return results

In [17]:
# VNEXPRESS
def get_page_urls_vnexpress(base_url, quantity):
    news_per_page = 25
    if quantity % news_per_page == 0:
        no_of_pages = quantity // news_per_page
    else:
        no_of_pages = quantity // news_per_page + 1

    extend_url = ['-p{}'.format(page) for page in range(2, no_of_pages + 1)]
    url_list = [base_url + extend_part for extend_part in extend_url]
    url_list.insert(0, base_url)
    return url_list

In [21]:
# THANHNIEN
def get_links_in_page_thanhnien(url):
    page = urllib.request.urlopen(url)
    soup = BeautifulSoup(page, 'html.parser')
    # <div>
    div_all = soup.find_all('div', attrs={'class':'site-content'})
    # div_all
    # <h2>
    h2_all = []
    for div in div_all:
        h2_all.extend(div.find_all('h2', attrs={'class':''}))
    # print(h2_all)
    #<a>
    a_all = []
    results = [[]]
    for h2 in h2_all:
        a_all.extend(h2.find_all('a', attrs={'class':'story__title'}))

    for a in a_all:
        title = a.get('title')
        if(a.get('href').find('video') != -1):
            pass
        else:
            link =  'https://thanhnien.vn/'+ str(a.get('href'))

        print('Title: {} - Link: {}'.format(title, link))
        results.append([title,link])
    return results

In [24]:
# THANHNIEN
def get_page_urls_thanhnien(base_url, quantity):
    news_per_page = 25
    if quantity % news_per_page == 0:
        no_of_pages = quantity // news_per_page
    else:
        no_of_pages = quantity // news_per_page + 1

    extend_url = ['/trang-{}.html'.format(page) for page in range(2, no_of_pages + 1)]
    url_list = [base_url + extend_part for extend_part in extend_url]
    url_list.insert(0, base_url)
    return url_list

In [7]:
# VIETNAMNET
def get_links_in_page_vietnamnet(url):
#     url = 'https://vietnamnet.vn/vn/thoi-su/trang5/'
    page = urllib.request.urlopen(url)
    soup = BeautifulSoup(page, 'html.parser')
    # <div>
    div_all = soup.find_all('div', attrs={'class':'list-content list-content-loadmore lagre m-t-20 clearfix'})
    div_all

    # <h3>
    h3_all = []
    for div in div_all:
        h3_all.extend(div.find_all('h3', attrs={'class':''}))
    #<a>
    a_all = []
    results = [[]]
    for h3 in h3_all:
        a_all.extend(h3.find_all('a'))
    # print(a_all)
    for a in a_all:
        title = a.get('title')
        link =  'https://vietnamnet.vn/vn/thoi-su'+ str(a.get('href'))
        print('Title: {} - Link: {}'.format(title, link))
        results.append([title,link])
    return results

In [1]:
# VIETNAMNET
def get_page_urls_vietnamnet(base_url, quantity):
    news_per_page = 25
    if quantity % news_per_page == 0:
        no_of_pages = quantity // news_per_page
    else:
        no_of_pages = quantity // news_per_page + 1

    extend_url = [f'trang{page}/' for page in range(2, no_of_pages + 1)]
    url_list = [base_url + extend_part for extend_part in extend_url]
    url_list.insert(0, base_url)
    return url_list

In [189]:
#################################################

In [16]:
def vnexpress(base_url):
    page_urls = get_page_urls_vnexpress(base_url, quantity=40000)
#     print(page_urls)
    total_articles = 0
    for page in page_urls:
        arr = get_links_in_page_vnexpress(page)
        for i in range(1,len(arr)-1):
            title = arr[i][0]
            url = arr[i][1]
            crawl_by_url(url,title)
# base_url = 'http://vnexpress.net/thoi-su' ## category = thoi-su

In [18]:
vnexpress('http://vnexpress.net/thoi-su')

Title: Đề xuất đặt tượng tướng Đồng Sỹ Nguyên ở nghĩa trang Trường Sơn - Link: https://vnexpress.net/de-xuat-dat-tuong-tuong-dong-sy-nguyen-o-nghia-trang-truong-son-4253666.html
Title: Ngư dân bốc mộ cá voi - Link: https://vnexpress.net/ngu-dan-boc-mo-ca-voi-4253401.html
Title: Nghiên cứu thí điểm buýt mini ở TP HCM - Link: https://vnexpress.net/nghien-cuu-thi-diem-buyt-mini-o-tp-hcm-4253486.html
Title: Hà Nội cấp một triệu thẻ căn cước công dân gắn chip - Link: https://vnexpress.net/ha-noi-cap-mot-trieu-the-can-cuoc-cong-dan-gan-chip-4254021.html
Title: TP HCM tiếp tục quảng cáo trên xe buýt - Link: https://vnexpress.net/tp-hcm-tiep-tuc-quang-cao-tren-xe-buyt-4253447.html
Title: Sà lan đứt neo đâm chìm 8 tàu cá - Link: https://vnexpress.net/sa-lan-dut-neo-dam-chim-8-tau-ca-4253399.html
Title: 'Tốn khoảng 4.500 tỷ đồng nếu đổi thẻ bảo hiểm y tế gắn chip' - Link: https://vnexpress.net/ton-khoang-4-500-ty-dong-neu-doi-the-bao-hiem-y-te-gan-chip-4253343.html
Title: 'Hình hài' quy hoạch bố

Title: An Giang cách ly hơn 60 người về từ Campuchia - Link: https://vnexpress.net/an-giang-cach-ly-hon-60-nguoi-ve-tu-campuchia-4251670.html
Title: Nhà phố cổ Hà Nội sẽ không quá 4 tầng - Link: https://vnexpress.net/nha-pho-co-ha-noi-se-khong-qua-4-tang-4251642.html
Title: Đoàn phụ nữ đi tham quan gặp nạn - Link: https://vnexpress.net/doan-phu-nu-di-tham-quan-gap-nan-4251640.html
Title: Hai cô gái rơi từ tầng cao chung cư - Link: https://vnexpress.net/hai-co-gai-roi-tu-tang-cao-chung-cu-4251615.html
Title: Người lao động khổ vì công ty nợ bảo hiểm xã hội - Link: https://vnexpress.net/nguoi-lao-dong-kho-vi-cong-ty-no-bao-hiem-xa-hoi-4249309.html
Title: 'Ba bài toán' quy hoạch đô thị sông Hồng - Link: https://vnexpress.net/ba-bai-toan-quy-hoach-do-thi-song-hong-4251236.html
Title: Bên trong trung tâm huấn luyện chó dữ - Link: https://vnexpress.net/ben-trong-trung-tam-huan-luyen-cho-du-4248678.html
Title: TP HCM đưa ra một loạt biện pháp chống 'cát tặc' - Link: https://vnexpress.net/tp-h

Title: TP HCM truy tìm một người Trung Quốc trốn khỏi khu cách ly - Link: https://vnexpress.net/tp-hcm-truy-tim-mot-nguoi-trung-quoc-tron-khoi-khu-cach-ly-4250522.html
Title: Đề xuất đầu tư cao tốc TP HCM - Chơn Thành 36.000 tỷ đồng - Link: https://vnexpress.net/de-xuat-dau-tu-cao-toc-tp-hcm-chon-thanh-36-000-ty-dong-4250442.html
Title: 77 người tự ứng cử đại biểu Quốc hội khóa mới - Link: https://vnexpress.net/77-nguoi-tu-ung-cu-dai-bieu-quoc-hoi-khoa-moi-4250346.html
Title: Cháy nhà hàng trong khu Thảo Điền - Link: https://vnexpress.net/chay-nha-hang-trong-khu-thao-dien-4250365.html
Title: Tạm giữ hai người Trung Quốc trốn khỏi khu cách ly - Link: https://vnexpress.net/tam-giu-hai-nguoi-trung-quoc-tron-khoi-khu-cach-ly-4250305.html
Title: Ông Nguyễn Thiện Nhân ứng cử đại biểu Quốc hội ở lĩnh vực khoa học - Link: https://vnexpress.net/ong-nguyen-thien-nhan-ung-cu-dai-bieu-quoc-hoi-o-linh-vuc-khoa-hoc-4250321.html
Title: Hơn 2.400 tân binh Hải Dương nhập ngũ - Link: https://vnexpress.n

Title: Hà Nội cho quán game, Internet hoạt động trở lại - Link: https://vnexpress.net/ha-noi-cho-quan-game-internet-hoat-dong-tro-lai-4248772.html
Title: Thu giữ hàng trăm thùng đạn - Link: https://vnexpress.net/thu-giu-hang-tram-thung-dan-4248698.html
Title: Đề xuất đầu tư 6 tuyến đường nối TP HCM với Long An - Link: https://vnexpress.net/de-xuat-dau-tu-6-tuyen-duong-noi-tp-hcm-voi-long-an-4248745.html
Title: Đứt cáp cần cẩu, hai người chết - Link: https://vnexpress.net/dut-cap-can-cau-hai-nguoi-chet-4248724.html
Title: Vì sao thẻ căn cước công dân mới được cấp 'xuyên đêm'? - Link: https://vnexpress.net/vi-sao-the-can-cuoc-cong-dan-moi-duoc-cap-xuyen-dem-4248299.html
Title: Lắp cửa van hơn 200 tấn cho cống ngăn mặn - Link: https://vnexpress.net/lap-cua-van-hon-200-tan-cho-cong-ngan-man-4248646.html
Title: Quốc hội dự kiến bầu tân Thủ tướng ngày 5/4 - Link: https://vnexpress.net/quoc-hoi-du-kien-bau-tan-thu-tuong-ngay-5-4-4248684.html
Title: CSGT TP HCM ra quân xử phạt xe cũ nát - Link

Title: Quảng Ninh cho quán karaoke, vũ trường hoạt động trở lại - Link: https://vnexpress.net/quang-ninh-cho-quan-karaoke-vu-truong-hoat-dong-tro-lai-4246607.html
Title: Thêm 9 địa điểm ở Cẩm Giàng hết phong tỏa - Link: https://vnexpress.net/them-9-dia-diem-o-cam-giang-het-phong-toa-4247154.html
Title: Chủ nhiệm Ủy ban Kiểm tra Trung ương được giới thiệu ứng cử Quốc hội - Link: https://vnexpress.net/chu-nhiem-uy-ban-kiem-tra-trung-uong-duoc-gioi-thieu-ung-cu-quoc-hoi-4246592.html
Title: Hải Phòng phong tỏa nhà riêng hai ca bệnh - Link: https://vnexpress.net/hai-phong-phong-toa-nha-rieng-hai-ca-benh-4246616.html
Title: 'Cơ cấu cán bộ diện Trung ương quản lý ngày càng trẻ hóa' - Link: https://vnexpress.net/co-cau-can-bo-dien-trung-uong-quan-ly-ngay-cang-tre-hoa-4246342.html
Title: Tiếp tục tìm kiếm 11 công nhân mất tích ở Rào Trăng - Link: https://vnexpress.net/tiep-tuc-tim-kiem-11-cong-nhan-mat-tich-o-rao-trang-4246567.html
Title: Xe đầu kéo tông liên hoàn - Link: https://vnexpress.net/

...

Title: Chủ tịch Đà Nẵng cầm cuốc cùng người dân dọn vệ sinh - Link: https://vnexpress.net/chu-tich-da-nang-cam-cuoc-cung-nguoi-dan-don-ve-sinh-3662303.html
Title: 1.000 tỷ mở đường nối đại lộ Thăng Long với quốc lộ 32 - Link: https://vnexpress.net/1-000-ty-mo-duong-noi-dai-lo-thang-long-voi-quoc-lo-32-3662298.html
Title: Chủ tịch Hà Nội kiểm tra việc di dời cây xanh đường Phạm Văn Đồng - Link: https://vnexpress.net/chu-tich-ha-noi-kiem-tra-viec-di-doi-cay-xanh-duong-pham-van-dong-3662284.html
Title: Học sinh Sài Gòn sẽ nghỉ Tết 16 ngày - Link: https://vnexpress.net/hoc-sinh-sai-gon-se-nghi-tet-16-ngay-3662293.html
Title: Hiệu trưởng cao đẳng mất chức vì sai phạm hơn 8 tỷ đồng - Link: https://vnexpress.net/hie-u-truo-ng-cao-dang-mat-chuc-vi-sai-pham-hon-8-ty-dong-3662290.html
Title: Sơn La công bố chỉ dẫn địa lý sản phẩm cà phê - Link: https://vnexpress.net/son-la-cong-bo-chi-dan-dia-ly-san-pham-ca-phe-3662275.html
Title: Hầm chui trăm tỷ ở Đà Nẵng kịp phục vụ APEC - Link: https://vne

Title: Sở Giáo dục Hà Giang phủ nhận việc không trọng dụng thủ khoa - Link: https://vnexpress.net/so-giao-duc-ha-giang-phu-nhan-viec-khong-trong-dung-thu-khoa-3661224.html
Title: Ba nhóm nguyên nhân khiến Metro Sài Gòn tăng vốn 30.000 tỷ đồng - Link: https://vnexpress.net/ba-nhom-nguyen-nhan-khien-metro-sai-gon-tang-von-30-000-ty-dong-3661288.html
Title: TP HCM tiếp tục ứng gần 1.200 tỷ đồng 'cứu' tuyến metro số 1 - Link: https://vnexpress.net/tp-hcm-tiep-tuc-ung-gan-1-200-ty-dong-cuu-tuyen-metro-so-1-3661261.html
Title: An ninh thắt chặt ngày BOT Biên Hòa thu phí trở lại - Link: https://vnexpress.net/an-ninh-that-chat-ngay-bot-bien-hoa-thu-phi-tro-lai-3661251.html
Title: Nhiều người tháo chạy khi ôtô bốc cháy trong nhà - Link: https://vnexpress.net/nhieu-nguoi-thao-chay-khi-oto-boc-chay-trong-nha-3661264.html
Title: Ba toà nhà tái định cư ở Hà Nội bị đề xuất phá bỏ - Link: https://vnexpress.net/ba-toa-nha-tai-dinh-cu-o-ha-noi-bi-de-xuat-pha-bo-3661160.html
Title: Người Hà Nội lội bùn 

Title: Nữ sinh khuyết tật ở Sài Gòn bị nhiều trường từ chối - Link: https://vnexpress.net/nu-sinh-khuyet-tat-o-sai-gon-bi-nhieu-truong-tu-choi-3659919.html
Title: Đạn lạc găm trúng người già, trẻ nhỏ ở Vĩnh Phúc - Link: https://vnexpress.net/dan-lac-gam-trung-nguoi-gia-tre-nho-o-vinh-phuc-3659892.html
Title: Cá chình 'khủng' 14 kg dính câu trong lòng hồ thủy điện - Link: https://vnexpress.net/ca-chinh-khung-14-kg-dinh-cau-trong-long-ho-thuy-dien-3659907.html
Title: Chủ tịch Yên Bái cam kết kỷ luật cán bộ sai phạm về tài sản - Link: https://vnexpress.net/chu-tich-yen-bai-cam-ket-ky-luat-can-bo-sai-pham-ve-tai-san-3659853.html
Title: Truy điệu hai cán bộ biên phòng bị lũ cuốn - Link: https://vnexpress.net/truy-dieu-hai-can-bo-bien-phong-bi-lu-cuon-3659851.html
Title: Nhiều vườn thanh long Bình Thuận bị lũ nhấn chìm - Link: https://video.vnexpress.net/tin-tuc/thoi-su/nhieu-vuon-thanh-long-binh-thuan-bi-lu-nhan-chim-3659856.html
Title: Ủy ban Văn hóa: 'Cá cược là nhu cầu thực tiễn nhưng nh

Title: Cô giáo dạy Địa lý bằng tiếng Anh - Link: https://vnexpress.net/co-giao-day-dia-ly-bang-tieng-anh-3658510.html
Title: Phận dâu Việt 'mười ba bến nước' xứ người - Link: https://vnexpress.net/phan-dau-viet-muoi-ba-ben-nuoc-xu-nguoi-3657795.html
Title: Thu phí ôtô vào nội đô TP HCM như thế nào - Link: https://vnexpress.net/thu-phi-oto-vao-noi-do-tp-hcm-nhu-the-nao-3658628.html
Title: Nghệ An 10 người chết, thiệt hại hơn 700 tỷ đồng do mưa lũ - Link: https://vnexpress.net/nghe-an-10-nguoi-chet-thiet-hai-hon-700-ty-dong-do-mua-lu-3658992.html
Title: Cả nước có trên 160 nghìn ôtô hết hạn sử dụng - Link: https://vnexpress.net/ca-nuoc-co-tren-160-nghin-oto-het-han-su-dung-3658924.html
Title: Hà Nội vá đê vỡ ở Chương Mỹ - Link: https://video.vnexpress.net/tin-tuc/thoi-su/ha-noi-va-de-vo-o-chuong-my-3658324.html
Title: Nữ cảnh sát đặc nhiệm luyện khí công, võ thuật trước APEC - Link: https://vnexpress.net/nu-canh-sat-dac-nhiem-luyen-khi-cong-vo-thuat-truoc-apec-3658839.html
Title: Tổng bí

ArticleException: Article `download()` failed with HTTPSConnectionPool(host='vnexpress.net', port=443): Read timed out. (read timeout=7) on URL https://vnexpress.net/nu-canh-sat-dac-nhiem-luyen-khi-cong-vo-thuat-truoc-apec-3658839.html

In [22]:
def thanhnien(base_url):
    page_urls = get_page_urls_thanhnien(base_url, quantity=10000)

    total_articles = 0
    for page in page_urls:
        arr = get_links_in_page_thanhnien(page)
        for i in range(1,len(arr)-1):
            title = arr[i][0]
            url = arr[i][1]
            crawl_by_url(url,title)
# base_url = 'http://thanhnien.vn/thoi-su' ## category = thoi-su

In [25]:
thanhnien('http://thanhnien.vn/thoi-su')

Title: Cần Thơ: Vì sao 'trùm xã hội đen’ Chín Xuân cho đàn em đốt nhà đội trưởng đội CSHS?  - Link: https://thanhnien.vn//thoi-su/can-tho-vi-sao-trum-xa-hoi-den-chin-xuan-cho-dan-em-dot-nha-doi-truong-doi-cshs-1360323.html
Title: 'Loạn cào cào' đặt tên thẩm mỹ viện, viện thẩm mỹ, trung tâm thẩm mỹ - Link: https://thanhnien.vn//thoi-su/loan-cao-cao-dat-ten-tham-my-vien-vien-tham-my-trung-tam-tham-my-1360409.html
Title: Ngày mai 29.3, PC06 TP.HCM tạm dừng nhận hồ sơ cấp căn cước công dân gắn chip - Link: https://thanhnien.vn//thoi-su/ngay-mai-293-pc06-tphcm-tam-dung-nhan-ho-so-cap-can-cuoc-cong-dan-gan-chip-1360412.html
Title: Bắt quả tang nhóm thanh niên rải và dán hàng ngàn tờ rơi ‘tín dụng đen' - Link: https://thanhnien.vn//thoi-su/bat-qua-tang-nhom-thanh-nien-rai-va-dan-hang-ngan-to-roi-tin-dung-den-1360407.html
Title: Cơ quan an ninh điều tra đang làm rõ vụ 'góp siêu tốc' 3.597 tỉ đồng vào Saigon Co.op - Link: https://thanhnien.vn//thoi-su/co-quan-an-ninh-dieu-tra-dang-lam-ro-vu-gop

Title: Cần Thơ: Vì sao 'trùm xã hội đen’ Chín Xuân cho đàn em đốt nhà đội trưởng đội CSHS?  - Link: https://thanhnien.vn//thoi-su/can-tho-vi-sao-trum-xa-hoi-den-chin-xuan-cho-dan-em-dot-nha-doi-truong-doi-cshs-1360323.html
Title: 'Loạn cào cào' đặt tên thẩm mỹ viện, viện thẩm mỹ, trung tâm thẩm mỹ - Link: https://thanhnien.vn//thoi-su/loan-cao-cao-dat-ten-tham-my-vien-vien-tham-my-trung-tam-tham-my-1360409.html
Title: Ngày mai 29.3, PC06 TP.HCM tạm dừng nhận hồ sơ cấp căn cước công dân gắn chip - Link: https://thanhnien.vn//thoi-su/ngay-mai-293-pc06-tphcm-tam-dung-nhan-ho-so-cap-can-cuoc-cong-dan-gan-chip-1360412.html
Title: Bắt quả tang nhóm thanh niên rải và dán hàng ngàn tờ rơi ‘tín dụng đen' - Link: https://thanhnien.vn//thoi-su/bat-qua-tang-nhom-thanh-nien-rai-va-dan-hang-ngan-to-roi-tin-dung-den-1360407.html
Title: Cơ quan an ninh điều tra đang làm rõ vụ 'góp siêu tốc' 3.597 tỉ đồng vào Saigon Co.op - Link: https://thanhnien.vn//thoi-su/co-quan-an-ninh-dieu-tra-dang-lam-ro-vu-gop

Title: Cần Thơ: Vì sao 'trùm xã hội đen’ Chín Xuân cho đàn em đốt nhà đội trưởng đội CSHS?  - Link: https://thanhnien.vn//thoi-su/can-tho-vi-sao-trum-xa-hoi-den-chin-xuan-cho-dan-em-dot-nha-doi-truong-doi-cshs-1360323.html
Title: 'Loạn cào cào' đặt tên thẩm mỹ viện, viện thẩm mỹ, trung tâm thẩm mỹ - Link: https://thanhnien.vn//thoi-su/loan-cao-cao-dat-ten-tham-my-vien-vien-tham-my-trung-tam-tham-my-1360409.html
Title: Ngày mai 29.3, PC06 TP.HCM tạm dừng nhận hồ sơ cấp căn cước công dân gắn chip - Link: https://thanhnien.vn//thoi-su/ngay-mai-293-pc06-tphcm-tam-dung-nhan-ho-so-cap-can-cuoc-cong-dan-gan-chip-1360412.html
Title: Bắt quả tang nhóm thanh niên rải và dán hàng ngàn tờ rơi ‘tín dụng đen' - Link: https://thanhnien.vn//thoi-su/bat-qua-tang-nhom-thanh-nien-rai-va-dan-hang-ngan-to-roi-tin-dung-den-1360407.html
Title: Cơ quan an ninh điều tra đang làm rõ vụ 'góp siêu tốc' 3.597 tỉ đồng vào Saigon Co.op - Link: https://thanhnien.vn//thoi-su/co-quan-an-ninh-dieu-tra-dang-lam-ro-vu-gop

Title: Cần Thơ: Vì sao 'trùm xã hội đen’ Chín Xuân cho đàn em đốt nhà đội trưởng đội CSHS?  - Link: https://thanhnien.vn//thoi-su/can-tho-vi-sao-trum-xa-hoi-den-chin-xuan-cho-dan-em-dot-nha-doi-truong-doi-cshs-1360323.html
Title: 'Loạn cào cào' đặt tên thẩm mỹ viện, viện thẩm mỹ, trung tâm thẩm mỹ - Link: https://thanhnien.vn//thoi-su/loan-cao-cao-dat-ten-tham-my-vien-vien-tham-my-trung-tam-tham-my-1360409.html
Title: Ngày mai 29.3, PC06 TP.HCM tạm dừng nhận hồ sơ cấp căn cước công dân gắn chip - Link: https://thanhnien.vn//thoi-su/ngay-mai-293-pc06-tphcm-tam-dung-nhan-ho-so-cap-can-cuoc-cong-dan-gan-chip-1360412.html
Title: Bắt quả tang nhóm thanh niên rải và dán hàng ngàn tờ rơi ‘tín dụng đen' - Link: https://thanhnien.vn//thoi-su/bat-qua-tang-nhom-thanh-nien-rai-va-dan-hang-ngan-to-roi-tin-dung-den-1360407.html
Title: Cơ quan an ninh điều tra đang làm rõ vụ 'góp siêu tốc' 3.597 tỉ đồng vào Saigon Co.op - Link: https://thanhnien.vn//thoi-su/co-quan-an-ninh-dieu-tra-dang-lam-ro-vu-gop

Title: Cần Thơ: Vì sao 'trùm xã hội đen’ Chín Xuân cho đàn em đốt nhà đội trưởng đội CSHS?  - Link: https://thanhnien.vn//thoi-su/can-tho-vi-sao-trum-xa-hoi-den-chin-xuan-cho-dan-em-dot-nha-doi-truong-doi-cshs-1360323.html
Title: 'Loạn cào cào' đặt tên thẩm mỹ viện, viện thẩm mỹ, trung tâm thẩm mỹ - Link: https://thanhnien.vn//thoi-su/loan-cao-cao-dat-ten-tham-my-vien-vien-tham-my-trung-tam-tham-my-1360409.html
Title: Ngày mai 29.3, PC06 TP.HCM tạm dừng nhận hồ sơ cấp căn cước công dân gắn chip - Link: https://thanhnien.vn//thoi-su/ngay-mai-293-pc06-tphcm-tam-dung-nhan-ho-so-cap-can-cuoc-cong-dan-gan-chip-1360412.html
Title: Bắt quả tang nhóm thanh niên rải và dán hàng ngàn tờ rơi ‘tín dụng đen' - Link: https://thanhnien.vn//thoi-su/bat-qua-tang-nhom-thanh-nien-rai-va-dan-hang-ngan-to-roi-tin-dung-den-1360407.html
Title: Cơ quan an ninh điều tra đang làm rõ vụ 'góp siêu tốc' 3.597 tỉ đồng vào Saigon Co.op - Link: https://thanhnien.vn//thoi-su/co-quan-an-ninh-dieu-tra-dang-lam-ro-vu-gop

...

Title: Thủ tướng Nguyễn Xuân Phúc: Tiếp tục nghiên cứu luật Đặc khu - Link: https://thanhnien.vn//thoi-su/thu-tuong-nguyen-xuan-phuc-tiep-tuc-nghien-cuu-luat-dac-khu-1360367.html
Title: Công an TP.Đồng Xoài bắt giữ đối tượng cầm đầu vụ bắt, giữ người trái pháp luật - Link: https://thanhnien.vn//thoi-su/cong-an-tpdong-xoai-bat-giu-doi-tuong-cam-dau-vu-bat-giu-nguoi-trai-phap-luat-1360443.html
Title: Giám đốc Công an tỉnh nói gì về vụ án mạng tại quán nhậu Lương Sơn Quán? - Link: https://thanhnien.vn//thoi-su/giam-doc-cong-an-tinh-noi-gi-ve-vu-an-mang-tai-quan-nhau-luong-son-quan-1360349.html
Title: Khám chữa bệnh không phép, một người nước ngoài bị phạt, thu hồi hơn nửa tỉ đồng - Link: https://thanhnien.vn//thoi-su/kham-chua-benh-khong-phep-mot-nguoi-nuoc-ngoai-bi-phat-thu-hoi-hon-nua-ti-dong-1360439.html
Title: Một học sinh đuối nước ở Bình Định: Chỗ tai nạn là nơi khai thác cát trái phép? - Link: https://thanhnien.vn//thoi-su/mot-hoc-sinh-duoi-nuoc-o-binh-dinh-cho-tai-nan-la-noi-khai-

Title: Thủ tướng Nguyễn Xuân Phúc: Tiếp tục nghiên cứu luật Đặc khu - Link: https://thanhnien.vn//thoi-su/thu-tuong-nguyen-xuan-phuc-tiep-tuc-nghien-cuu-luat-dac-khu-1360367.html
Title: Công an TP.Đồng Xoài bắt giữ đối tượng cầm đầu vụ bắt, giữ người trái pháp luật - Link: https://thanhnien.vn//thoi-su/cong-an-tpdong-xoai-bat-giu-doi-tuong-cam-dau-vu-bat-giu-nguoi-trai-phap-luat-1360443.html
Title: Giám đốc Công an tỉnh nói gì về vụ án mạng tại quán nhậu Lương Sơn Quán? - Link: https://thanhnien.vn//thoi-su/giam-doc-cong-an-tinh-noi-gi-ve-vu-an-mang-tai-quan-nhau-luong-son-quan-1360349.html
Title: Khám chữa bệnh không phép, một người nước ngoài bị phạt, thu hồi hơn nửa tỉ đồng - Link: https://thanhnien.vn//thoi-su/kham-chua-benh-khong-phep-mot-nguoi-nuoc-ngoai-bi-phat-thu-hoi-hon-nua-ti-dong-1360439.html
Title: Một học sinh đuối nước ở Bình Định: Chỗ tai nạn là nơi khai thác cát trái phép? - Link: https://thanhnien.vn//thoi-su/mot-hoc-sinh-duoi-nuoc-o-binh-dinh-cho-tai-nan-la-noi-khai-

Title: Thủ tướng Nguyễn Xuân Phúc: Tiếp tục nghiên cứu luật Đặc khu - Link: https://thanhnien.vn//thoi-su/thu-tuong-nguyen-xuan-phuc-tiep-tuc-nghien-cuu-luat-dac-khu-1360367.html
Title: Công an TP.Đồng Xoài bắt giữ đối tượng cầm đầu vụ bắt, giữ người trái pháp luật - Link: https://thanhnien.vn//thoi-su/cong-an-tpdong-xoai-bat-giu-doi-tuong-cam-dau-vu-bat-giu-nguoi-trai-phap-luat-1360443.html
Title: Giám đốc Công an tỉnh nói gì về vụ án mạng tại quán nhậu Lương Sơn Quán? - Link: https://thanhnien.vn//thoi-su/giam-doc-cong-an-tinh-noi-gi-ve-vu-an-mang-tai-quan-nhau-luong-son-quan-1360349.html
Title: Khám chữa bệnh không phép, một người nước ngoài bị phạt, thu hồi hơn nửa tỉ đồng - Link: https://thanhnien.vn//thoi-su/kham-chua-benh-khong-phep-mot-nguoi-nuoc-ngoai-bi-phat-thu-hoi-hon-nua-ti-dong-1360439.html
Title: Một học sinh đuối nước ở Bình Định: Chỗ tai nạn là nơi khai thác cát trái phép? - Link: https://thanhnien.vn//thoi-su/mot-hoc-sinh-duoi-nuoc-o-binh-dinh-cho-tai-nan-la-noi-khai-

Title: Thủ tướng Nguyễn Xuân Phúc: Tiếp tục nghiên cứu luật Đặc khu - Link: https://thanhnien.vn//thoi-su/thu-tuong-nguyen-xuan-phuc-tiep-tuc-nghien-cuu-luat-dac-khu-1360367.html
Title: Công an TP.Đồng Xoài bắt giữ đối tượng cầm đầu vụ bắt, giữ người trái pháp luật - Link: https://thanhnien.vn//thoi-su/cong-an-tpdong-xoai-bat-giu-doi-tuong-cam-dau-vu-bat-giu-nguoi-trai-phap-luat-1360443.html
Title: Giám đốc Công an tỉnh nói gì về vụ án mạng tại quán nhậu Lương Sơn Quán? - Link: https://thanhnien.vn//thoi-su/giam-doc-cong-an-tinh-noi-gi-ve-vu-an-mang-tai-quan-nhau-luong-son-quan-1360349.html
Title: Khám chữa bệnh không phép, một người nước ngoài bị phạt, thu hồi hơn nửa tỉ đồng - Link: https://thanhnien.vn//thoi-su/kham-chua-benh-khong-phep-mot-nguoi-nuoc-ngoai-bi-phat-thu-hoi-hon-nua-ti-dong-1360439.html
Title: Một học sinh đuối nước ở Bình Định: Chỗ tai nạn là nơi khai thác cát trái phép? - Link: https://thanhnien.vn//thoi-su/mot-hoc-sinh-duoi-nuoc-o-binh-dinh-cho-tai-nan-la-noi-khai-

KeyboardInterrupt: 

In [10]:
def vietnamnet(base_url):
    page_urls = get_page_urls_vietnamnet(base_url, quantity=300)
#     print(page_urls)
    for page in page_urls:
        arr = get_links_in_page_vietnamnet(page)
        for i in range(1,len(arr)-1):
            title = arr[i][0]
            url = arr[i][1]
            crawl_by_url(url,title)

# base_url = 'https://vietnamnet.vn/vn/thoi-su/' ## category = thoi-su

In [237]:
vietnamnet('https://vietnamnet.vn/vn/thoi-su/')

Title: Tiết lộ mỗi cây hoa ban ở 'trái tim thành Vinh' giá 13 triệu đồng - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/tiet-lo-moi-cay-hoa-ban-o-trai-tim-thanh-vinh-gia-13-trieu-dong-722425.html
Title: Trăn trở của Đại biểu Dương Trung Quốc trước khi rời Quốc hội - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/chinh-tri/tran-tro-cua-dai-bieu-duong-trung-quoc-truoc-khi-roi-ghe-quoc-hoi-722643.html
Title: TP.HCM gỡ phong tỏa nhà trọ liên quan ca nhập cảnh trái phép cùng BN2580 - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/go-phong-toa-nha-tro-lien-quan-ca-nhap-canh-trai-phep-cung-bn2580-722627.html
Title: Thiếu nữ tử vong thương tâm sau va chạm với xe đầu kéo trên QL51 - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/thieu-nu-tu-vong-thuong-tam-sau-va-cham-voi-xe-dau-keo-tren-ql51-722599.html
Title: Xe Limousine tự tông vào dải phân cách, hai người thoát chết trên cao tốc - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/o-to-limousine-tong-vao-dai-phan-cach-hai-nguo

Title: Hai cô gái ẩu đả, thanh niên cầm dao náo loạn phố Hồng Mai, Hà Nội - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/clip-nong/hai-co-gai-au-da-thanh-nien-cam-dao-nao-loan-pho-hong-mai-ha-noi-722150.html
Title: Hà Nội: Thêm huyện Thanh Oai muốn lên quận - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/ha-noi-them-huyen-thanh-oai-muon-len-quan-721873.html
Title: Chánh án Nguyễn Hòa Bình: Nhiệm kỳ qua không có người nào bị kết án oan - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/chinh-tri/chanh-an-nguyen-hoa-binh-nhiem-ky-qua-khong-co-nguoi-nao-bi-ket-an-oan-722235.html
Title: Ô tô khách phanh 'cháy lốp' vẫn tông vào xe máy khiến 3 người thương vong - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/an-toan-giao-thong/o-to-khach-phanh-chay-lop-van-tong-vao-xe-may-khien-3-nguoi-thuong-vong-722141.html
Title: Chuyển giao nhân sự, chuẩn bị cho nhiệm kỳ mới tốt hơn - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/quoc-hoi/chuyen-giao-nhan-su-chuan-bi-cho-nhiem-ky-moi-to

Title: Vụ lật xe 7 người chết: Vừa về tới nhà thì nghe tin mẹ gặp nạn - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/an-toan-giao-thong/vu-lat-xe-7-nguoi-chet-vua-ve-toi-nha-thi-nghe-tin-me-gap-nan-721758.html
Title: Dự án cầu Thủ Thiêm 2 sẽ khai thác vào năm 2022 - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/an-toan-giao-thong/du-an-cau-thu-thiem-2-se-khai-thac-vao-nam-2022-721744.html
Title: Phó Thủ tướng chia buồn với gia đình nạn nhân vụ tai nạn ở Thanh Hoá - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/an-toan-giao-thong/tai-nan-o-thanh-hoa-pho-thu-tuong-gui-loi-chia-buon-voi-gia-dinh-nan-nhan-721742.html
Title: CSGT vượt hàng chục km giúp cô gái tìm lại 100 triệu đồng bỏ quên trên xe khách - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/csgt-vuot-hang-chuc-km-giup-co-gai-tim-lai-100-trieu-dong-bo-quen-tren-xe-khach-721680.html
Title: TP Thủ Đức được giao thu ngân sách hơn 8.300 tỷ đồng - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/tp-thu-duc-duoc-giao-th

Title: Người phụ nữ tử vong sau va chạm với xe khách ở Quảng Trị - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/an-toan-giao-thong/nguoi-phu-nu-tu-vong-sau-va-cham-voi-xe-khach-o-quang-tri-721236.html
Title: Xử trí thông minh của lính biên phòng trước màn hóa trang vượt biên tinh vi - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/quoc-phong/xu-tri-thong-minh-cua-linh-bien-phong-truoc-man-hoa-trang-vuot-bien-tinh-vi-721216.html
Title: Nghi vấn hai cô gái tử vong do rơi lầu chung cư ở Sài Gòn - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/nghi-van-hai-co-gai-tu-vong-do-roi-lau-chung-cu-o-sai-gon-721197.html
Title: Một người tử vong trong vụ xe container đâm loạt ô tô rơi xuống vực - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/an-toan-giao-thong/mot-nguoi-tu-vong-trong-vu-xe-container-dam-loat-o-to-roi-xuong-vuc-721151.html
Title: Bắt 5 người Trung Quốc nhập cảnh trái phép vào Việt Nam - Link: https://vietnamnet.vn/vn/thoi-su/vn/thoi-su/bat-5-nguoi-trung-quoc-nhap-canh